# Part B: Dataset Selection

## Existing Dataset: Financial Phrasebank

For this project, we chose to utilize the Financial PhraseBank dataset available through the Hugging Face datasets library: https://huggingface.co/datasets/financial_phrasebank?row=3. The Financial PhraseBank dataset is a collection of financial news headlines annotated with sentiment labels, making it suitable for sentiment analysis tasks in the domain of finance.

Reasons for Choosing Financial PhraseBank:

1. **Domain Relevance**: The dataset consists of financial news headlines, which are highly relevant to our task of sentiment analysis of ASX stocks. Analyzing sentiment in financial news headlines can provide valuable insights for investors and traders.

2. **Annotation Quality**: The Financial PhraseBank dataset provides sentiment labels for each news headline, allowing for supervised learning approaches to be applied effectively. These annotations enable us to train machine learning models to predict sentiment with a certain level of accuracy.

3. **Availability and Accessibility**: The dataset is readily available through the Hugging Face datasets library, making it a convenient option. Additionally, the dataset is well-documented, providing clear guidelines on data usage and annotations.

4. **Size and Diversity**: While the Financial PhraseBank dataset may not be as large as some other sentiment analysis datasets, it offers a diverse range of financial news headlines covering various topics and sentiments. 

## Creating Our Own Dataset

In addition to utilizing the Financial PhraseBank dataset, we created a custom dataset by scraping news articles for companies listed in the ASX200 index. This custom dataset was obtained by querying the NewsAPI to retrieve news articles published within the past 30 days related to these companies.

Reasons for Creating a Custom Dataset:

1. **Comparison and Evaluation**: We decided to create our own dataset to compare and evaluate our sentiment analysis models against a different set of data. By using a custom dataset in addition to the Financial PhraseBank, we can assess the robustness and generalisation capabilities of our models across different sources of data.

2. **Coverage of ASX200 Companies**: The ASX200 index comprises Australia's top 200 publicly listed companies by market capitalization. By scraping news articles specifically related to these companies, we aim to capture sentiment trends and insights relevant to the Australian stock market.

3. **Freshness of Data**: The custom dataset includes news articles published within the past 30 days, ensuring that the data is up-to-date and reflects recent developments and sentiments in the financial landscape.

4. **Flexibility and Control**: Creating our own dataset gives us flexibility in terms of selecting the companies to focus on and controlling the data collection process. This allows us to tailor the dataset to our specific research needs and objectives.

## Step 1: Getting A List of the ASX200 Companies

In [2]:
# imports
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.common.action_chains import ActionChains
from selenium.webdriver.chrome.options import Options
import time
import pandas as pd
import os
from newsapi import NewsApiClient
import pandas as pd
from datetime import datetime, timedelta
from transformers import LongformerTokenizer, EncoderDecoderModel
import torch
import numpy as np
from transformers import BertTokenizer, BertForSequenceClassification, pipeline

In the cell below, the Selenium WebDriver is initialised, and the URL of the Market Index webpage containing the ASX-listed companies is specified. The script navigates to the specified URL using the WebDriver. A loop is executed to iterate through each row of the table containing the company information. For each row, the XPath of the company code element is dynamically constructed, and the corresponding element is located using Selenium's WebDriverWait. The text content of the located element (company code) is extracted and appended to a list of company codes. Exception handling is implemented to handle any errors that may occur during the scraping process. This includes handling general exceptions and stopping the scraping loop if an error occurs. After scraping is complete, the script prints the list of company codes extracted from the webpage. Finally, the WebDriver is closed to release system resources.

In [60]:
driver = webdriver.Chrome()

url = "https://www.marketindex.com.au/asx-listed-companies"

driver.get(url)

wait = WebDriverWait(driver, 10)

company_codes = []

try:
    for i in range(1, 201):  
        xpath = f"/html/body/div[1]/div[2]/div/div[1]/div/div/div/div/div[2]/div/div/div/div/table/tbody/tr[{i}]/td[3]/a"
        try:
            company_code_element = wait.until(
                EC.element_to_be_clickable((By.XPATH, xpath))
            )
            company_code = company_code_element.text.strip()
            company_codes.append(company_code)
            ActionChains(driver).move_to_element(company_code_element).perform()
            if i % 10 == 0:
                time.sleep(2)  

        except Exception as e:
            print(f"Stopped at iteration {i} due to an exception: {e}")
            break  
except Exception as general_exception:
    print(f"General Error during scraping: {general_exception}")

for code in company_codes:
    print(code)

driver.quit()

BHP
CBA
CSL
NAB
WBC
ANZ
FMG
WES
MQG
GMG
WDS
RIO
TLS
TCL
WOW
WTC
ALL
QBE
JHX
STO
REA
BXB
COL
COH
SUN
XRO
REH
RMD
SCG
NST
ORG
CPU
IAG
VAS
S32
SVW
FPH
MIN
SHL
CAR
SOL
ASX
RHC
PLS
PME
PMGOLD
TLC
SGP
AIA
APA
BSL
TWE
MPL
QAN
NEM
EDV
ALD
AFI
VCX
MGR
AMC
SEK
WOR
MCY
ORI
ALU
NXT
GPT
IFT
TPG
DXS
ALX
EVN
SPK
IVV
VGS
YAL
AZJ
GQG
JBH
MEZ
BLD
ARG
ALQ
MGOC
WHC
SDF
EBO
HVN
CWY
AGL
CHC
QUB
VEA
IGO
BEN
LYC
QUAL
TNE
IPL
IOZ
STW
DACE
NWL
PMV
FLT
CGF
IEL
A200
SQ2
PDN
LLC
NDQ
AWC
VTS
RWC
MTS
CSR
A2M
BKW
NHC
SFR
TLX
BOQ
DGCE
DMP
BRG
NHF
NIC
LOV
VHY
CIA
BPT
GOLD
SUL
APE
IOO
HUB
AAA
WEB
ANN
DOW
LTR
ARB
MGF
NSR
VNT
AUB
AMP
ETHI
PRU
ILU
VEU
CNU
VAP
VGAD
ORA
SMR
FBU
PPT
360
AVZ
DFGH
BFL
NEU
RGN
CLW
NEC
LNW
HDN
LTM
HYGG
DRR
NABPH
DEG
SNZ
CTD
VUK
SGM
BWP
HMC
GNE
PNI
IAF
BGL
VDHG
MP1
MVW
RMS
GMD
EMR
HBRD
MXT
CIP
BAP
PXA
SIG
MFF
NABPI
ABC


This function takes a list of company codes as input and saves them to a CSV file. It creates a pandas DataFrame from the list of company codes and then writes the DataFrame to a CSV file "comanycodes.csv".

In [63]:
def convert_and_save_to_csv(company_codes, file_name="companycodes.csv"):
    print("Converting and saving company codes to CSV...")
    df_company_codes = pd.DataFrame(company_codes, columns=["Company Code"])
    current_dir = os.getcwd()
    file_path = os.path.join(current_dir, file_name)
    df_company_codes.to_csv(file_path, index=False)
    return file_path

In [64]:
print("Length of company_codes:", len(company_codes))
print("First few company codes:", company_codes[:5])

converted_file_path = convert_and_save_to_csv(company_codes)
print(f"File saved at: {converted_file_path}")

Length of company_codes: 200
First few company codes: ['BHP', 'CBA', 'CSL', 'NAB', 'WBC']
Converting and saving company codes to CSV...
File saved at: /Users/priyal/COMP6713/Stock-Analysis-Tool/companycodes.csv


## Step 2: Get Article URLs For Each Stock Code

The script below initialises a NewsAPI client using an API key obtained from the NewsAPI website. Company codes are read from a CSV file containing ASX-listed company codes. A date range spanning the past 30 days is defined to fetch articles published within this timeframe. For each company code, the script queries the NewsAPI to retrieve news articles published within the specified date range. The articles are sorted by publication date. The fetched article data, including the company code, title, description, and URL, is stored in a DataFrame. The DataFrame containing the article data is saved to a CSV file named "articles1.csv", "articles2.csv", "articles3.csv". These csv files were combined into combined_articles.csv.

Notes:
- The script stops fetching articles if it encounters a specific company code ("IPL"). This is because the free plan for NewsAPI only allows hundred API pings per account.
- Ensure that you replace `"enter_an_api_key"` with your actual NewsAPI key obtained from the NewsAPI website.

In [83]:
newsapi = NewsApiClient(
    api_key="enter_an_api_key"
)  # register at https://newsapi.org/account to get an api key

company_codes_df = pd.read_csv("companycodes.csv")

today = datetime.now().date()
start_date = today - timedelta(days=30)
end_date = today

def fetch_articles(company_code):
    print(f"Fetching articles for {company_code}")
    articles = newsapi.get_everything(
        q=company_code,
        from_param=start_date.strftime("%Y-%m-%d"),
        to=end_date.strftime("%Y-%m-%d"),
        language="en",
        sort_by="publishedAt",
    )
    return articles


article_data = []

stop_extraction = False
for company_code in company_codes_df["Company Code"]:
    if company_code == "IPL":
        stop_extraction = True
        break

    articles = fetch_articles(company_code)

    for article in articles["articles"]:
        article_data.append(
            {
                "Company Code": company_code,
                "Title": article["title"],
                "Description": article["description"],
                "URL": article["url"],
            }
        )

articles_df = pd.DataFrame(article_data)

articles_df.to_csv("articles1.csv", index=False)
print("Articles saved to 'articles.csv'")

Fetching articles for BHP
Fetching articles for CBA
Fetching articles for CSL
Fetching articles for NAB
Fetching articles for WBC
Fetching articles for ANZ
Fetching articles for FMG
Fetching articles for WES
Fetching articles for MQG
Fetching articles for GMG
Fetching articles for WDS
Fetching articles for RIO
Fetching articles for TLS
Fetching articles for TCL
Fetching articles for WOW
Fetching articles for WTC
Fetching articles for ALL
Fetching articles for QBE
Fetching articles for JHX
Fetching articles for STO
Fetching articles for REA
Fetching articles for BXB
Fetching articles for COL
Fetching articles for COH
Fetching articles for SUN
Fetching articles for XRO
Fetching articles for REH
Fetching articles for RMD
Fetching articles for SCG
Fetching articles for NST
Fetching articles for ORG
Fetching articles for CPU
Fetching articles for IAG
Fetching articles for VAS
Fetching articles for S32
Fetching articles for SVW
Fetching articles for FPH
Fetching articles for MIN
Fetching art

## Step 3: Scraping and Updating DataFrame with Article Content

The code initializes a headless Chrome WebDriver using Selenium's ChromeOptions to run in headless mode, i.e., without opening a visible browser window.The `scrape_content` function is defined to scrape the content of a news article from its URL. It uses Selenium to navigate to the URL, waits for the body element to be present, and then extracts the text content from paragraph elements ( `<p>` tags) on the page. The `scrape_and_update_dataframe` function reads a CSV file containing article data into a DataFrame. It then applies the `scrape_content` function to each URL in the DataFrame's "URL" column, scraping the content and adding it to a new "Content" column in the DataFrame. Finally, the updated DataFrame is saved back to the same CSV file, overwriting the original data.

Notes:
- Ensure that the Chrome WebDriver executable is installed and accessible in the system PATH.
- Error handling is implemented to handle exceptions that may occur during the scraping process, ensuring that the script continues execution even if some URLs fail to be scraped.
- For ease, I ran the code for half the URLs at a time.
- **This took 440 minutes to run.**
- **PLEASE COLLAPSE THE OUTPUT FOR THE FOLLOWING CELLS AS IT IS VERY LONG**

In [85]:
chrome_options = Options()
chrome_options.add_argument("--headless")  
driver = webdriver.Chrome(
    options=chrome_options
)  
wait = WebDriverWait(driver, 10)

def scrape_content(url):
    try:
        driver.get(url)
        body_element = wait.until(EC.presence_of_element_located((By.TAG_NAME, "body")))
        paragraphs = body_element.find_elements(By.TAG_NAME, "p")
        content = " ".join([p.text.strip() for p in paragraphs])
        return content
    except Exception as e:
        print(f"Error scraping content from {url}: {e}")
        return ""

def scrape_and_update_dataframe(csv_file):
    df = pd.read_csv(csv_file)
    df["Content"] = df["URL"].apply(scrape_content)
    df.to_csv(csv_file, index=False)

csv_file_path = "articles1.csv"
scrape_and_update_dataframe(csv_file_path)

Error scraping content from https://financialpost.com/pmn/business-wire-news-releases-pmn/northisle-announces-issuance-of-share-based-compensation-2: Message: stale element reference: stale element not found in the current frame
  (Session info: chrome-headless-shell=123.0.6312.123); For documentation on this error, please visit: https://www.selenium.dev/documentation/webdriver/troubleshooting/errors#stale-element-reference-exception
Stacktrace:
0   chromedriver                        0x0000000104524474 chromedriver + 4326516
1   chromedriver                        0x000000010451c93c chromedriver + 4294972
2   chromedriver                        0x0000000104148088 chromedriver + 278664
3   chromedriver                        0x000000010414cabc chromedriver + 297660
4   chromedriver                        0x000000010414e428 chromedriver + 304168
5   chromedriver                        0x000000010414e4a0 chromedriver + 304288
6   chromedriver                        0x0000000104185a28 chr

The code below scrapes the other half of the URLs. **This too took 425 minutes to fully run.**

**PLEASE COLLAPSE THE OUTPUT FOR THE FOLLOWING CELLS AS IT IS VERY LONG**

In [86]:
chrome_options = Options()
chrome_options.add_argument("--headless") 
driver = webdriver.Chrome(
    options=chrome_options
)  
wait = WebDriverWait(driver, 10)


def scrape_content(url):
    try:
        driver.get(url)
        body_element = wait.until(EC.presence_of_element_located((By.TAG_NAME, "body")))
        paragraphs = body_element.find_elements(By.TAG_NAME, "p")
        content = " ".join([p.text.strip() for p in paragraphs])
        return content
    except Exception as e:
        print(f"Error scraping content from {url}: {e}")
        return ""

def scrape_and_update_dataframe(csv_file):
    df = pd.read_csv(csv_file)
    df["Content"] = df["URL"].apply(scrape_content)
    df.to_csv(csv_file, index=False)

csv_file_path = "articles2.csv"
scrape_and_update_dataframe(csv_file_path)

Error scraping content from https://journals.plos.org/plosone/article?id=10.1371/journal.pone.0301290: Message: stale element reference: stale element not found in the current frame
  (Session info: chrome-headless-shell=123.0.6312.123); For documentation on this error, please visit: https://www.selenium.dev/documentation/webdriver/troubleshooting/errors#stale-element-reference-exception
Stacktrace:
0   chromedriver                        0x00000001050f4474 chromedriver + 4326516
1   chromedriver                        0x00000001050ec93c chromedriver + 4294972
2   chromedriver                        0x0000000104d18088 chromedriver + 278664
3   chromedriver                        0x0000000104d1cabc chromedriver + 297660
4   chromedriver                        0x0000000104d1e428 chromedriver + 304168
5   chromedriver                        0x0000000104d1e4a0 chromedriver + 304288
6   chromedriver                        0x0000000104d55a28 chromedriver + 530984
7   chromedriver            

This is a method to efficiently filter financial articles based on specific keywords, facilitating the extraction of relevant content for further analysis or processing. The filtering process involves removing rows with empty content and selecting articles that contain specific keywords related to stock market analysis, trading, investments, and other financial topics.

In [ ]:
df = pd.read_csv("articles3.csv") #change to articles1.csv, articles2.csv
num_rows_before = len(df)
keywords = [
    "stock market",
    "trading",
    "stocks",
    "equity",
    "investments",
    "financial markets",
    "market analysis",
    "portfolio management",
    "investment strategies",
    "market trends",
    "economic indicators",
    "asset allocation",
    "risk management",
    "market volatility",
    "fundamental analysis",
    "technical analysis",
    "market news",
    "market updates",
    "stock prices",
    "market performance",
]

# Remove rows with empty content
df = df.dropna(subset=["Content"])

filtered_df = df[
    df.apply(
        lambda row: any(
            (isinstance(row["Title"], str) and keyword in row["Title"].lower())
            or (
                isinstance(row["Description"], str)
                and keyword in row["Description"].lower()
            )
            or (isinstance(row["Content"], str) and keyword in row["Content"].lower())
            or (isinstance(row["Company Code"], str) and keyword in row["Company Code"])
            for keyword in keywords
        ),
        axis=1,
    )
]

num_rows_after = len(filtered_df)

filtered_df.to_csv("filtered_csv_file3.csv", index=False)

Combining all the CSV files into one large CSV file.

In [ ]:
file_paths = ["articles1.csv", "articles2.csv", "articles3.csv"]

dfs = []

for file_path in file_paths:
    df = pd.read_csv(file_path)
    dfs.append(df)

concatenated_df = pd.concat(dfs, ignore_index=True)

print(len(concatenated_df))

concatenated_df.to_csv("combined_articles_orig.csv", index=False)

## Step 4: Summarise The Articles' Content

Similar to the Financial PhraseBank dataset and to make it simpler for our models to run, we chose to summarise the content that we scraped for each URL.
The below code initializes a Longformer tokenizer and an Encoder-Decoder model using the Hugging Face `transformers` library. This code was written with reference to the Week 5 demos for COMP6713.

In [6]:
tokenizer = LongformerTokenizer.from_pretrained("allenai/longformer-base-4096")
model = EncoderDecoderModel.from_pretrained(
    "patrickvonplaten/longformer2roberta-cnn_dailymail-fp16"
)
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model.to(device)

config.json:   0%|          | 0.00/3.52k [00:00<?, ?B/s]

You are using a model of type encoder_decoder to instantiate a model of type encoder-decoder. This is not supported for all configurations of models and can yield errors.


pytorch_model.bin:   0%|          | 0.00/1.21G [00:00<?, ?B/s]

Some weights of the model checkpoint at patrickvonplaten/longformer2roberta-cnn_dailymail-fp16 were not used when initializing EncoderDecoderModel: ['decoder.roberta.pooler.dense.bias', 'decoder.roberta.pooler.dense.weight', 'encoder.embeddings.position_ids']
- This IS expected if you are initializing EncoderDecoderModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing EncoderDecoderModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


EncoderDecoderModel(
  (encoder): LongformerModel(
    (embeddings): LongformerEmbeddings(
      (word_embeddings): Embedding(50265, 768, padding_idx=1)
      (token_type_embeddings): Embedding(1, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
      (position_embeddings): Embedding(4098, 768, padding_idx=1)
    )
    (encoder): LongformerEncoder(
      (layer): ModuleList(
        (0-11): 12 x LongformerLayer(
          (attention): LongformerAttention(
            (self): LongformerSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (query_global): Linear(in_features=768, out_features=768, bias=True)
              (key_global): Linear(in_features=768, out_features=768, bias=True)
              (value_global):

The below function `split_text_into_chunks` splits a given text into smaller chunks of a specified maximum length. This functionality is useful when dealing with long sequences of text, such as the longer articles.

In [ ]:
df = pd.read_csv("combined_articles.csv")

def split_text_into_chunks(text, max_chunk_length=4096):
    chunks = []
    for i in range(0, len(text), max_chunk_length):
        chunks.append(text[i : i + max_chunk_length])
    return chunks

The code iterates through each row of the DataFrame, extracting the article content and company code. For each article, the content is split into smaller chunks using the `split_text_into_chunks` function to accommodate model input limitations. The article content and company code are concatenated, and the resulting text is tokenized using the Longformer tokeniser. The tokenised input is fed into the Encoder-Decoder model for summary generation. The model generates a summary for each chunk of the article content. The individual summaries generated for each chunk are concatenated to form a complete summary for the article. The generated summaries are stored in a new column ("Summary") in the DataFrame. The DataFrame with article content, company codes, and generated summaries is saved to a new CSV file, which I later renamed to final-data.csv.


**PLEASE COLLAPSE THE OUTPUT FOR THE FOLLOWING CELL AS IT IS VERY LONG**

In [22]:
for index, row in df.iterrows():
    article_content = row["Content"]
    company_code = row["Company Code"]

    if isinstance(article_content, str) and not article_content.strip():
        summary = np.nan
    else:

        content_chunks = split_text_into_chunks(article_content)

        summaries = []
        for chunk in content_chunks:

            input_text = f"{chunk} {company_code}"

            input_ids = tokenizer(input_text, return_tensors="pt").input_ids.to(device)

            with torch.no_grad():
                output_ids = model.generate(input_ids)

            summary = tokenizer.decode(output_ids[0], skip_special_tokens=True)

            summaries.append(summary)

        summary = " ".join(summaries)

    print(f"Summary for article {index + 1}: {summary}")
    df.at[index, "Summary"] = summary

df.to_csv("combined_articles_with_summaries.csv", index=False)

You are using a model of type encoder_decoder to instantiate a model of type encoder-decoder. This is not supported for all configurations of models and can yield errors.
Some weights of the model checkpoint at patrickvonplaten/longformer2roberta-cnn_dailymail-fp16 were not used when initializing EncoderDecoderModel: ['decoder.roberta.pooler.dense.bias', 'decoder.roberta.pooler.dense.weight', 'encoder.embeddings.position_ids']
- This IS expected if you are initializing EncoderDecoderModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing EncoderDecoderModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


Summary for article 1: Shell's Chief Executive Wael Sawan says he is looking at "all options"
Shares in Shell rose 0.9% to 2,839 pence each in London on Tuesday morning.
Sawan is in the midst of a "sprint" of 10 quarters to cut costs, he said.


Input ids are automatically padded from 917 to 1024 to be a multiple of `config.attention_window`: 512


Summary for article 2: Australian shares end higher on Tuesday as iron ore prices rise.
Gold prices rise 0.5% as prices rise on hopes for improved demand in China.
Australia's consumer sentiment for April dipped.
New Zealand's benchmark S&P/NZX 50 index sheds 0.4% to end day at 11,916.78.


Input ids are automatically padded from 462 to 512 to be a multiple of `config.attention_window`: 512
Input ids are automatically padded from 898 to 1024 to be a multiple of `config.attention_window`: 512


...

Summary for article 2321: APA Corporation has completed its acquisition of Callon Petroleum Company.
The move will enhance its operations in the Permian Basin.
APA's stock has experienced a strong return over the last month.
CEO John J. Christmann says the acquisition aligns with its strategy. InvestingPro is a yearly or bi-yearly Pro and Pro+ subscription.
The company is also a Pro-Pro+ subscription provider.
A year-long or biyearly subscription is available at InvestingPro.
Investingpro is the UK's only or bi yearly Pro & Pro+ Pro+.
Summary for article 2322: APA Corp. announced acquisition of Callon Petroleum Company.
Callon stock is no longer listed on the NYSE.
Company owns consolidated subsidiaries that explore for and produce oil and natural gas.
The acquisition will bring APA's daily reported production to approximately 500,000 barrels of oil equivalent (BOE) APA-G GlobeNewswire: "Risk factors" could cause our results to differ from others.
APA and its subsidiaries undertake no 

Input ids are automatically padded from 377 to 512 to be a multiple of `config.attention_window`: 512


Summary for article 2331: NFL Network is letting go of four on-air personalities.
The move is part of a deal to bring the network back to Los Angeles.
ESPN Network is cutting its staff and is cutting off staff.
Jimmy Traina's Sports Illustrated sports podcast is returning.
Sports Illustrated is returning to its sports journalism podcast. New Orleans' pioneering nonprofit The Lens is a case study for the nonprofit sector.
The Lens is the first peer to learn about the newsroom as a case-study.
Poynter will speak about the nonprofit as a possible case study.
Read the Poynters' weekly media newsletter on CNN.com.
Summary for article 2332: The Kraft Heinz Company (NASDAQ:KHC – Free Report) lessened its stake in The Kraft Heinze Company (Free Report)
The firm recently declared a quarterly dividend, which was paid on Friday, and six months later.
The company recently declared its quarterly dividend.
and six-month high.
Shares were paid a $0.40 per share. Snowflake Inc. shares Gap Management L

Input ids are automatically padded from 228 to 512 to be a multiple of `config.attention_window`: 512


Summary for article 2336: Bruce Lehrmann launched defamation case against Network Ten and journalist Lisa Wilkinson.
The defamation case is returning to the Federal Court on Thursday and Friday.
Media commentator Stephen Mayne says the case has put focus on culture at the Seven Network.
Seven Network spokesman says Seven did not reimburse Bruce Lehrman for expenses. Seven Network Network agreed to pay Mr Lehrmann's rent for a year.
The Seven Network has denied the allegations.
Mr Lehrman's interview with the Seven Network cost $4,000 a fortnight.
He believes the allegations of inappropriate expenditure are damaging people's trust in the media. The standard does not apply to journalists who are not members of the MEAA.
The standard doesn't apply to media outlets.
It is copyright and cannot be reproduced.
This service may include material from Agence France-Presse (AFP) and APTN.
Summary for article 2337: Comedian Charlamagne tha God blasted diversity, equity and inclusion programs.
He s

# Step 5: Labelling The Dataset

Below, we perform sentiment analysis on financial data using the FinancialBERT model. We utilise the `BertForSequenceClassification` model and the `BertTokenizer` from the `transformers` library to classify the sentiment of textual data into three categories: negative, neutral, and positive. 

We initialise the `BertForSequenceClassification` model and its corresponding tokenizer using the pre-trained weights from the `"ahmedrachid/FinancialBERT-Sentiment-Analysis"` model.

In [1]:
model = BertForSequenceClassification.from_pretrained(
    "ahmedrachid/FinancialBERT-Sentiment-Analysis", num_labels=3
)
tokenizer = BertTokenizer.from_pretrained(
    "ahmedrachid/FinancialBERT-Sentiment-Analysis"
)

nlp = pipeline("sentiment-analysis", model=model, tokenizer=tokenizer)

df = pd.read_excel("final-data.xlsx")


def apply_bert_sentiment(text):
    if pd.isna(text):
        return None  
    inputs = tokenizer(text, return_tensors="pt", max_length=512, truncation=True)
    outputs = model(**inputs)
    sentiment = int(outputs.logits.argmax())
    if sentiment == 0:
        return "negative"
    elif sentiment == 1:
        return "neutral"
    else:
        return "positive"


df["Sentiment"] = df["Summary"].apply(apply_bert_sentiment)
df.to_excel("final-data-updated.xlsx", index=False)